# Choropleth Map: Coronavirus

The objective of this notebook is to create a **choropleth map** with the cases of the coronavirus on March 05, 2020. 

In [28]:
import geopandas as gpd
import json
from bokeh.io import show
from bokeh.models import (CDSView, ColorBar, ColumnDataSource,
                          CustomJS, CustomJSFilter, 
                          GeoJSONDataSource, HoverTool,
                          LinearColorMapper, Slider, LogColorMapper)
from bokeh.layouts import column, row, widgetbox
from bokeh.palettes import brewer
from bokeh.plotting import figure
from bokeh.io import output_notebook
output_notebook()
import pandas as pd
from shapely.geometry import Point, Polygon
import shapely.wkt
import seaborn as sns
from bokeh.models import LinearColorMapper, FixedTicker, ColorBar, NumeralTickFormatter
from bokeh.plotting import figure, output_file, save
from bokeh.io import export_png
from bokeh.plotting import figure, show, output_file
from bokeh.tile_providers import get_provider, Vendors

Loading BokehJS ...

In [3]:
path = '/Users/cblanesg/Downloads/CHGIS_V4_1990_PROV_PGN-shapefile'

In [4]:
data_shapefiles = gpd.read_file(path)

In [4]:
## Check what CRS has the data 
data_shapefiles.crs
#data_shapefiles = data_shapefiles.to_crs('epsg:4326') ## Change CRS if it's necessary. 

{'init': 'epsg:4326'}

In [5]:
data_shapefiles.head()

GBCODE90    NAME_PY NAME_HZ  SDE2_CHGIS  SDE2_CHG_1    SHAPE_AREA  \
0   340000      Anhui  å®å¾½         0.0         0.0  1.413467e+11   
1   110000    Beijing  åäº¬         0.0         0.0  1.671717e+10   
2   350000     Fujian  ç¦å»º         0.0         0.0  1.230045e+11   
3   620000      Gansu  çè
         0.0         0.0  4.128726e+11   
4   440000  Guangdong  å»£æ±         0.0         0.0  1.774517e+11   

      SHAPE_LEN                                           geometry  
0  2.924949e+06  POLYGON ((117.65244 29.61467, 117.64326 29.609...  
1  7.741163e+05  POLYGON ((116.68565 41.01808, 116.67989 41.009...  
2  4.389994e+06  MULTIPOLYGON (((117.45581 23.78605, 117.44966 ...  
3  7.403188e+06  POLYGON ((105.38684 32.84258, 105.39461 32.834...  
4  5.754889e+06  MULTIPOLYGON (((115.54111 22.78858, 115.53045 ...

In [7]:
## Make a GeoJSON
geosource = GeoJSONDataSource(geojson = data_shapefiles.to_json())

In [8]:
## Download cases of coronavirus
path_info = '/Users/cblanesg/cam.blanes Dropbox/Camila Blanes/deep_dive/GIS/COVID-19/csse_covid_19_data/csse_covid_19_time_series/time_series_19-covid-Confirmed.csv'

In [11]:
info = pd.read_csv(path_info)
info = info[(info['Country/Region'] == 'Mainland China')]
test_info = info[['Province/State', 'Lat', 'Long',
                 '3/5/20']]
test_info.head()

Province/State      Lat      Long  3/5/20
0          Anhui  31.8257  117.2264     990
1        Beijing  40.1824  116.4142     418
2      Chongqing  30.0572  107.8740     576
3         Fujian  26.0789  117.9874     296
4          Gansu  36.0611  103.8343     102

In [13]:
casos = gpd.GeoDataFrame(
test_info, geometry = gpd.points_from_xy(test_info.Long, test_info.Lat))

In [14]:
#### Making sure that the data from the csv has the same CRS of the shapefiles!!
casos['geometry'].crs = {'init' : 'epsg:4326'}

In [22]:
data_shapefiles['geometry'].crs

{'init': 'epsg:4326'}

## Find the polygon that corresponds to the coordinate point

In [15]:
list_points = []
for x,y in zip(test_info.Long, test_info.Lat):
    list_points.append(Point(x,y))

In [17]:
new_dict = {}
for x, y in zip(list_points, test_info['3/5/20']):
    if str(x) not in new_dict:
        new_dict[str(x)] = y

In [18]:
list_poly = data_shapefiles.geometry.tolist()

In [19]:
dict_polygons = {}
n = 0
for point in list_points:
    n += 1
    if n % 500 == 0:
        print(n)
    for polygon in list_poly:
        if str(polygon) not in dict_polygons:
            dict_polygons[str(polygon)] = []
        if point.within(polygon):
            dict_polygons[str(polygon)].append(point) 
            break

In [20]:
dict_polygons = {}
n = 0
for point,y in zip(casos['geometry'], casos['3/5/20']):
    #n += 1
    #if n % 500 == 0:
     #   print(n)
    for polygon in list_poly:
        if str(polygon) not in dict_polygons:
            dict_polygons[str(polygon)] = []
        if point.within(polygon):
            dict_polygons[str(polygon)].append(y) 
            break

In [21]:
dict_density = {}
for number, polygon in enumerate(list_poly):
    if str(number) not in dict_density:
        dict_density[str(number)] = 0

In [22]:
x = [0, 6, 5]
for i, j in enumerate(x):
    print(i, j)

0 0
1 6
2 5


In [23]:
for point,value in zip(casos['geometry'], casos['3/5/20']):
    for number, polygon in enumerate(list_poly):
        if point.within(polygon):
            dict_density[str(number)] += value
            continue

In [25]:
number_of_cases = []
geometries = []
for keys, values in dict_density.items():
    number_of_cases.append(values)
    geometries.append(list_poly[int(keys)])

In [26]:
d = {'casos': number_of_cases, 'geometry': geometries}
df = pd.DataFrame(data=d)

## 

In [29]:
geo_shape = gpd.GeoDataFrame(df)
geo_shape.crs = {'init' : 'epsg:4326'}
geo_shape = geo_shape.to_crs(epsg = 3395)
geosource2 = GeoJSONDataSource(geojson = geo_shape.to_json())

/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/pyproj/crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))


In [30]:
p1 = figure(title = 'Confirmed Cases of Coronavirus (China: March 05, 2020) ', 
           plot_height = 800, plot_width = 800, 
           toolbar_location = 'below',
           tools = 'pan, wheel_zoom, box_zoom, reset')
    
p1.xgrid.grid_line_color = None
p1.ygrid.grid_line_color = None
p1.xaxis.major_label_text_color = None
p1.yaxis.major_label_text_color = None
palette = sns.color_palette('Blues', 9)
palette = palette.as_hex()

#palette = palette2[::-1]

tile_provider = get_provider(Vendors.CARTODBPOSITRON_RETINA)# range bounds supplied in web mercator coordinates

p1.add_tile(tile_provider)


color_mapper = LogColorMapper(palette = palette, low = 0, high = 67110)
china = p1.patches('xs', 'ys', source = geosource2,
                        fill_color = {'field' : 'casos', 'transform' : color_mapper},
                      line_color = None,
                      line_width = 0.7,
                      fill_alpha = 1)
p1.add_tools(HoverTool(renderers = [china],
                     tooltips = [('Número de Casos', '@casos')]))

color_bar = ColorBar(color_mapper = color_mapper, ticker = FixedTicker(ticks=[0, 1, 5, 20, 85, 300, 1000 ,5000 ,20000 , 67110]),
                     location=(0,0), orientation="horizontal")

p1.add_layout(color_bar, 'below')
#output_file("china_coronavirus.html")
#save(p1)
show(p1)